In [1]:
import math
import argparse
import os
import shutil
import time
import numpy as np
import sys
from collections import OrderedDict

import tensorflow as tf

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.nn.parallel
import torch.backends.cudnn as cudnn
import torch.optim
import torch.utils.data
import torchvision.transforms as transforms
import torchvision.datasets as datasets
from torch.autograd import Variable
from torch.autograd import Function

# used for logging to TensorBoard
from tensorboard_logger import configure, log_value

/home/jwserver/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
# shake-shake special functions
class ShakeFunction(Function):
    @staticmethod
    def forward(ctx, x1, x2, alpha, beta):
        ctx.save_for_backward(x1, x2, alpha, beta)

        y = x1 * alpha + x2 * (1 - alpha)
        return y

    @staticmethod
    def backward(ctx, grad_output):
        x1, x2, alpha, beta = ctx.saved_variables
        grad_x1 = grad_x2 = grad_alpha = grad_beta = None

        if ctx.needs_input_grad[0]:
            grad_x1 = grad_output * beta
        if ctx.needs_input_grad[1]:
            grad_x2 = grad_output * (1 - beta)

        return grad_x1, grad_x2, grad_alpha, grad_beta


shake_function = ShakeFunction.apply


def get_alpha_beta(batch_size, shake_config, is_cuda, device=None):
    forward_shake, backward_shake, shake_image = shake_config

    if forward_shake and not shake_image:
        alpha = torch.rand(1)
    elif forward_shake and shake_image:
        alpha = torch.rand(batch_size).view(batch_size, 1, 1, 1)
    else:
        alpha = torch.FloatTensor([0.5])

    if backward_shake and not shake_image:
        beta = torch.rand(1)
    elif backward_shake and shake_image:
        beta = torch.rand(batch_size).view(batch_size, 1, 1, 1)
    else:
        beta = torch.FloatTensor([0.5])

    if is_cuda:
        alpha = alpha.to(device)
        beta = beta.to(device)

    return alpha, beta

In [3]:
def initialize_weights(module):
    if isinstance(module, nn.Conv2d):
        nn.init.kaiming_normal_(module.weight.data, mode='fan_out')
    elif isinstance(module, nn.BatchNorm2d):
        module.weight.data.fill_(1)
        module.bias.data.zero_()
    elif isinstance(module, nn.Linear):
        module.bias.data.zero_()


class ResidualPath(nn.Module):
    def __init__(self, in_channels, out_channels, stride):
        super(ResidualPath, self).__init__()

        self.conv1 = nn.Conv2d(
            in_channels,
            out_channels,
            kernel_size=3,
            stride=stride,
            padding=1,
            bias=False,
        )
        self.bn1 = nn.BatchNorm2d(out_channels)
        self.conv2 = nn.Conv2d(
            out_channels,
            out_channels,
            kernel_size=3,
            stride=1,
            padding=1,
            bias=False)
        self.bn2 = nn.BatchNorm2d(out_channels)

    def forward(self, x):
        x = F.relu(x, inplace=False)
        x = F.relu(self.bn1(self.conv1(x)), inplace=False)
        x = self.bn2(self.conv2(x))
        return x


class DownsamplingShortcut(nn.Module):
    def __init__(self, in_channels):
        super(DownsamplingShortcut, self).__init__()
        self.conv1 = nn.Conv2d(
            in_channels,
            in_channels,
            kernel_size=1,
            stride=1,
            padding=0,
            bias=False)
        self.conv2 = nn.Conv2d(
            in_channels,
            in_channels,
            kernel_size=1,
            stride=1,
            padding=0,
            bias=False)
        self.bn = nn.BatchNorm2d(in_channels * 2)

    def forward(self, x):
        x = F.relu(x, inplace=False)
        y1 = F.avg_pool2d(x, kernel_size=1, stride=2, padding=0)
        y1 = self.conv1(y1)

        y2 = F.pad(x[:, :, 1:, 1:], (0, 1, 0, 1))
        y2 = F.avg_pool2d(y2, kernel_size=1, stride=2, padding=0)
        y2 = self.conv2(y2)

        z = torch.cat([y1, y2], dim=1)
        z = self.bn(z)

        return z


class BasicBlock(nn.Module):
    def __init__(self, in_channels, out_channels, stride, shake_config, device):
        super(BasicBlock, self).__init__()
        self.device = device

        self.shake_config = shake_config

        self.residual_path1 = ResidualPath(in_channels, out_channels, stride)
        self.residual_path2 = ResidualPath(in_channels, out_channels, stride)

        self.shortcut = nn.Sequential()
        if in_channels != out_channels:
            self.shortcut.add_module('downsample',
                                     DownsamplingShortcut(in_channels))

    def forward(self, x):
        x1 = self.residual_path1(x)
        x2 = self.residual_path2(x)

        if self.training:
            shake_config = self.shake_config
        else:
            shake_config = (False, False, False)

        alpha, beta = get_alpha_beta(x.size(0), shake_config, x.is_cuda, self.device)
        y = shake_function(x1, x2, alpha, beta)

        return self.shortcut(x) + y


class Network(nn.Module):
    def __init__(self, config, device):
        super(Network, self).__init__()
        self.device = device

        input_shape = config['input_shape']
        n_classes = config['n_classes']

        base_channels = config['base_channels']
        depth = config['depth']
        self.shake_config = (config['shake_forward'], config['shake_backward'],
                             config['shake_image'])

        block = BasicBlock
        n_blocks_per_stage = (depth - 2) // 6
        assert n_blocks_per_stage * 6 + 2 == depth

        n_channels = [base_channels, base_channels * 2, base_channels * 4]

        self.conv = nn.Conv2d(
            input_shape[1],
            n_channels[0],
            kernel_size=3,
            stride=1,
            padding=1,
            bias=False)
        self.bn = nn.BatchNorm2d(base_channels)

        self.stage1 = self._make_stage(
            n_channels[0], n_channels[0], n_blocks_per_stage, block, stride=1)
        self.stage2 = self._make_stage(
            n_channels[0], n_channels[1], n_blocks_per_stage, block, stride=2)
        self.stage3 = self._make_stage(
            n_channels[1], n_channels[2], n_blocks_per_stage, block, stride=2)

        # compute conv feature size
        with torch.no_grad():
            self.feature_size = self._forward_conv(
                torch.zeros(*input_shape)).view(-1).shape[0]

        self.fc = nn.Linear(self.feature_size, n_classes)

        # initialize weights
        self.apply(initialize_weights)

    def _make_stage(self, in_channels, out_channels, n_blocks, block, stride):
        stage = nn.Sequential()
        for index in range(n_blocks):
            block_name = 'block{}'.format(index + 1)
            if index == 0:
                stage.add_module(
                    block_name,
                    block(
                        in_channels,
                        out_channels,
                        stride=stride,
                        shake_config=self.shake_config,
                        device=self.device))
            else:
                stage.add_module(
                    block_name,
                    block(
                        out_channels,
                        out_channels,
                        stride=1,
                        shake_config=self.shake_config,
                        device=self.device))
        return stage

    def _forward_conv(self, x):
        x = F.relu(self.bn(self.conv(x)), inplace=True)
        x = self.stage1(x)
        x = self.stage2(x)
        x = self.stage3(x)
        x = F.adaptive_avg_pool2d(x, output_size=1)
        return x

    def forward(self, x):
        x = self._forward_conv(x)
        x = x.view(x.size(0), -1)
        x = self.fc(x)
        return x

In [4]:
hparam = dict()

# Dataset Configuration
hparam['dataset'] = 'FashionMNIST'				# Name of the dataset
hparam['classes'] = ['T-shirt/top', 'Trouser', 'Pullover', 'Dress', 'Coat',
                     'Sandal', 'Shirt', 'Sneaker', 'Bag', 'Ankle boot']		# List of classes
hparam['data_split'] = 30000					# Rearranging Train/Val Ratio (False if default)

# Training Configuration
hparam['print_freq'] = 10						# Print frequency
hparam['start_epoch'] = 0						# Manual Epoch number (useful on restarts)
hparam['resume'] = None							# Path to latest checkpoint
hparam['name'] = 'shake_shake-26(2x64d)'		# Name of experiment
hparam['tensorboard'] = False					# Log progress to Tensorboard
hparam['manual_seed'] = 40000					# Seed Number

# Transformation
hparam['cutout'] = True							# Whether to use cutout transform
hparam['cutout_size'] = 16						# Cutout size (Use ONLY if cutout is TRUE)
hparam['cutout_prob'] = 1						# Cutout probability (Use ONLY if cutout is TRUE)
hparam['cutout_inside'] = False					# Whether to use cutout inside (Use ONLY if cutout is TRUE)

# Hyperparameter Configuration
hparam['epochs'] = 1800							# Number of total epochs to run
hparam['batch_size'] = 256						# Mini-batch size (256 recommended for 1080ti)
hparam['lr'] = 0.1								# Initial Learning Rate
hparam['momentum'] = 0.9						# Momentum
hparam['nesterov'] = False						# Nesterov momentum
hparam['weight_decay'] = 1e-4					# Weight-decay
hparam['layers'] = 26							# Total number of layers
hparam['lr_min'] = 0							# Minimum learning rate

# Net Configuration
hparam['base_channels'] = 64					# Initial Channels to begin with (Choices:32, 64, 96)
hparam['shake_forward'] = True					# Shake Forward
hparam['shake_backward'] = True				# Shake Backward
hparam['shake_image'] = True					# Shake Images
hparam['input_shape'] = (1, 3, 32, 32)


# GPU Configuration
hparam['cuda_device'] = '1'						# Which GPU Devices to use (CPU: False)

# Hardward Usage
hparam['num_workers'] = 4						# Number of Workers

best_prec1 = 0

In [5]:
def main(hparam):
    global best_prec1
    
    if hparam['tensorboard']: configure("runs/%s"%(hparam['name']))
    
    torch.manual_seed(hparam['manual_seed'])
    print("Current CPU Random Seed: {}".format(torch.initial_seed()))
    
    device_nums = str(hparam['cuda_device']).strip('[]')
    device = torch.device("cuda:{}".format(device_nums)
                              if hparam['cuda_device'] else "cpu")
    
    if hparam['cuda_device']:
        torch.cuda.manual_seed_all(hparam['manual_seed'])
        print("Current GPU Random Seed: {}".format(torch.cuda.initial_seed()))
        
        
    if hparam["cutout"]:
        mean = np.array([0.2860])
        std = np.array([0.3530])
        transform = transforms.Compose([
            transforms.RandomCrop(28, padding=4),
            transforms.RandomHorizontalFlip(),
            image_normalize(mean, std),
            cutout(hparam['cutout_size'], hparam['cutout_prob'], hparam['cutout_inside']),
            image_to_tensor(),
        ])
    else:
        normalize = transforms.Normalize(mean=[x/255.0 for x in [125.3, 123.0, 113.9]],
                                 std=[x/255.0 for x in [63.0, 62.1, 66.7]])
        transform = transforms.Compose([
            transforms.ToTensor(),
            normalize
            ])

    # Load Dataset
    if hparam['data_split']:
        # Concat and Split Dataset into new Train/Val ratio
        (train_data, train_labels), (test_data, test_labels) = tf.keras.datasets.fashion_mnist.load_data()

        N = hparam['data_split']
        
        test_data = np.concatenate((test_data, train_data[N:]), axis=0)
        test_labels = np.concatenate((test_labels, train_labels[N:]), axis=0)
        
        train_data = train_data[:N]
        train_labels = train_labels[:N]
        
        train_data = torch.from_numpy(train_data).float()
        train_labels = torch.from_numpy(train_labels).long()
        test_data = torch.from_numpy(test_data).float()
        test_labels = torch.from_numpy(test_labels).long()
        
        print("Test Data:", test_data.shape)
        print("Train Data:", train_data.shape)
        
        train_dataset = torch.utils.data.TensorDataset(train_data.unsqueeze(1), train_labels)
        val_dataset = torch.utils.data.TensorDataset(test_data.unsqueeze(1), test_labels)

        print("(Rearranged)Train: {}\t Test: {}".format(len(train_dataset), len(val_dataset)))
        
    else:
        train_dataset = datasets.__dict__[hparam['dataset']](
            './data', train=True, download=True, transform=transform_test)
        val_dataset = datasets.__dict__[hparam['dataset']](
            './data', train=False, transform=transform_test)
    
    kwargs = {'num_workers': hparam['num_workers'], 'pin_memory': True}
    assert(hparam['dataset'] == 'FashionMNIST' or hparam['dataset'] == 'MNIST')
    
    # Import dataset to DataLoader
    train_loader = torch.utils.data.DataLoader(
        train_dataset, batch_size=hparam['batch_size'], shuffle=True, **kwargs)
    val_loader = torch.utils.data.DataLoader(
        val_dataset, batch_size=hparam['batch_size'], shuffle=True, **kwargs)
    
    # create model
    model_config = OrderedDict([
        ('arch', hparam['name']),
        ('depth', hparam['layers']),
        ('base_channels', hparam['base_channels']),
        ('shake_forward', hparam['shake_forward']),
        ('shake_backward', hparam['shake_backward']),
        ('shake_image', hparam['shake_image']),
        ('input_shape', (1, 1, 32, 32)),
        ('n_classes', len(hparam['classes'])),
    ])
    model = Network(model_config, device)

    # for training on multiple GPUs.
    # Use CUDA_VISIBLE_DEVICES=0,1 to specify which GPUs to use
    # WARNING: Multi-GPU Mode is not working properly for now...
    if type(hparam['cuda_device']) == list and len(hparam['cuda_device']) > 1:
        print('\n===> Training on Multi-GPU!')
        model = nn.DataParallel(model, device_ids=hparam['cuda_device'], dim=0)
    else:
        print('\n===> Training on Single-GPU!')
    model = model.to(device)
    
    # get the number of model parameters
    print('Number of model parameters: {}'.format(
        sum([p.data.nelement() for p in model.parameters()])))		# 47.75M Parameters expected

    # optionally resume from a checkpoint
    if hparam['resume']:
        if os.path.isfile(hparam['resume']):
            print("=> loading checkpoint '{}'".format(hparam['resume']))
            checkpoint = torch.load(hparam['resume'])
            hparam['start_epoch'] = checkpoint['epoch']
            best_prec1 = checkpoint['best_prec1']
            model.load_state_dict(checkpoint['state_dict'])
            print("=> loaded checkpoint '{}' (epoch {})"
                  .format(hparam['resume'], checkpoint['epoch']))
        else:
            print("=> no checkpoint found at '{}'".format(hparam['resume']))

    cudnn.benchmark = True

    # define loss function (criterion) and optimizer
    criterion = nn.CrossEntropyLoss().to(device)
    optimizer = torch.optim.SGD(model.parameters(), hparam['lr'],
                                momentum=hparam['momentum'],
                                nesterov = hparam['nesterov'],
                                weight_decay=hparam['weight_decay'])
    
    optim_config = OrderedDict([
        ('epochs', hparam['epochs']),
        ('batch_size', hparam['batch_size']),
        ('base_lr', hparam['lr']),
        ('weight_decay', hparam['weight_decay']),
        ('momentum', hparam['momentum']),
        ('nesterov', hparam['nesterov']),
        ('lr_min', hparam['lr_min']),
    ])
    optim_config['steps_per_epoch'] = len(train_loader)
    optimizer, scheduler = create_optimizer(model.parameters(), optim_config)

    start_time = time.time()
    
    for epoch in range(hparam['start_epoch'], hparam['epochs']):
        adjust_learning_rate(optimizer, epoch+1, hparam)

        # train for one epoch
        train(train_loader, model, criterion, optimizer, epoch, hparam)

        # evaluate on validation set
        prec1 = validate(val_loader, model, criterion, epoch, hparam)

        # remember best prec@1 and save checkpoint
        is_best = prec1 > best_prec1
        best_prec1 = max(prec1, best_prec1)
        save_checkpoint({
            'epoch': epoch + 1,
            'state_dict': model.state_dict(),
            'best_prec1': best_prec1,
        }, is_best, hparam)
    print('Best accuracy: ', best_prec1)
    
    end_time = time.time()
    end_s = (end_time - start_time) % 60
    end_h = (end_time - start_time) // 3600
    end_m = (end_time - start_time - end_s) % 3600
    print("[Total Time Elapsed: {:02d}h {:02d}m {:.2f}s]")

In [6]:
def train(train_loader, model, criterion, optimizer, epoch, scheduler, hparam):
    """Train for one epoch on the training set"""
    batch_time = AverageMeter()
    losses = AverageMeter()
    top1 = AverageMeter()
    
    # Device Mode
    device_nums = str(hparam['cuda_device']).strip('[]')
    device = torch.device("cuda:{}".format(device_nums)
                              if hparam['cuda_device'] else "cpu")

    # switch to train mode
    model.train()

    end = time.time()
    for i, (input, target) in enumerate(train_loader):
        scheduler.step()
        
        input = input.to(device)
        target = target.to(device, non_blocking=True)
        input_var = torch.autograd.Variable(input)
        target_var = torch.autograd.Variable(target)

        # compute output
        output = model(input_var)
        loss = criterion(output, target_var)

        # measure accuracy and record loss
        prec1 = accuracy(output.data, target, topk=(1,))[0]
        losses.update(loss.data.item(), input.size(0))
        top1.update(prec1.item(), input.size(0))

        # compute gradient and do SGD step
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        # measure elapsed time
        batch_time.update(time.time() - end)
        end = time.time()

        if i % hparam['print_freq'] == 0:
            print('Epoch: [{0}][{1}/{2}]\t'
                  'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                  'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
                  'Prec@1 {top1.val:.3f} ({top1.avg:.3f})'.format(
                      epoch, i, len(train_loader), batch_time=batch_time,
                      loss=losses, top1=top1))
    # log to TensorBoard
    if hparam['tensorboard']:
        log_value('train_loss', losses.avg, epoch)
        log_value('train_acc', top1.avg, epoch)

In [7]:
def validate(val_loader, model, criterion, epoch, hparam):
    """Perform validation on the validation set"""
    batch_time = AverageMeter()
    losses = AverageMeter()
    top1 = AverageMeter()
    
    # Device Mode
    device_nums = str(hparam['cuda_device']).strip('[]')
    device = torch.device("cuda:{}".format(device_nums)
                              if hparam['cuda_device'] else "cpu")

    # switch to evaluate mode
    model.eval()

    end = time.time()
    for i, (input, target) in enumerate(val_loader):
        input = input.to(device)
        target = target.to(device, non_blocking=True)
        input_var = torch.autograd.Variable(input)
        target_var = torch.autograd.Variable(target)

        # compute output
        with torch.no_grad():
            output = model(input_var)
        loss = criterion(output, target_var)

        # measure accuracy and record loss
        prec1 = accuracy(output.data, target, topk=(1,))[0]
        losses.update(loss.data.item(), input.size(0))
        top1.update(prec1.item(), input.size(0))

        # measure elapsed time
        batch_time.update(time.time() - end)
        end = time.time()

        if i % hparam['print_freq'] == 0:
            print('Test: [{0}/{1}]\t'
                  'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                  'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
                  'Prec@1 {top1.val:.3f} ({top1.avg:.3f})'.format(
                      i, len(val_loader), batch_time=batch_time, loss=losses,
                      top1=top1))

    print(' * Prec@1 {top1.avg:.3f}'.format(top1=top1))
    # log to TensorBoard
    if hparam['tensorboard']:
        log_value('val_loss', losses.avg, epoch)
        log_value('val_acc', top1.avg, epoch)
    return top1.avg

In [8]:
def save_checkpoint(state, is_best, hparam, filename='checkpoint.pth.tar'):
    """Saves checkpoint to disk"""
    directory = "runs/{}/".format(hparam['name'])
    if not os.path.exists(directory):
        os.makedirs(directory)
    filename = directory + filename
    torch.save(state, filename)
    if is_best:
        shutil.copyfile(filename, 'runs/%s/'%(hparam['name']) + 'model_best.pth.tar')

In [9]:
class AverageMeter(object):
    """Computes and stores the average and current value"""
    def __init__(self):
        self.reset()

    def reset(self):
        self.val = 0
        self.avg = 0
        self.sum = 0
        self.count = 0

    def update(self, val, n=1):
        self.val = val
        self.sum += val * n
        self.count += n
        self.avg = self.sum / self.count

In [10]:
def cosine_annealing(step, total_steps, lr_max, lr_min):
    return lr_min + (lr_max - lr_min) * 0.5 * (
        1 + np.cos(step / total_steps * np.pi))

def _get_optimizer(model_parameters, optim_config):
    optimizer = torch.optim.SGD(
        model_parameters,
        lr=optim_config['base_lr'],
        momentum=optim_config['momentum'],
        weight_decay=optim_config['weight_decay'],
        nesterov=optim_config['nesterov'])
    return optimizer


def _get_scheduler(optimizer, optim_config):
    total_steps = optim_config['epochs'] * optim_config['steps_per_epoch']

    scheduler = torch.optim.lr_scheduler.LambdaLR(
        optimizer,
        lr_lambda=lambda step: cosine_annealing(
            step,
            total_steps,
            1,  # since lr_lambda computes multiplicative factor
            optim_config['lr_min'] / optim_config['base_lr']))
    return scheduler


def create_optimizer(model_parameters, optim_config):
    optimizer = _get_optimizer(model_parameters, optim_config)
    scheduler = _get_scheduler(optimizer, optim_config)
    return optimizer, scheduler

In [11]:
def image_to_tensor():
    def _to_tensor(image):
        if len(image.shape) == 3:
            return torch.from_numpy(
                image.transpose(2, 0, 1).astype(np.float32))
        else:
            return torch.from_numpy(image[None, :, :].astype(np.float32))

    return _to_tensor


def image_normalize(mean, std):
    mean = np.array(mean)
    std = np.array(std)

    def _normalize(image):
        image = np.asarray(image).astype(np.float32) / 255.
        image = (image - mean) / std
        return image

    return _normalize


def cutout(mask_size, p, cutout_inside, mask_color=0):
    mask_size_half = mask_size // 2
    offset = 1 if mask_size % 2 == 0 else 0

    def _cutout(image):
        image = np.asarray(image).copy()

        if np.random.random() > p:
            return image

        h, w = image.shape[:2]

        if cutout_inside:
            cxmin, cxmax = mask_size_half, w + offset - mask_size_half
            cymin, cymax = mask_size_half, h + offset - mask_size_half
        else:
            cxmin, cxmax = 0, w + offset
            cymin, cymax = 0, h + offset

        cx = np.random.randint(cxmin, cxmax)
        cy = np.random.randint(cymin, cymax)
        xmin = cx - mask_size_half
        ymin = cy - mask_size_half
        xmax = xmin + mask_size
        ymax = ymin + mask_size
        xmin = max(0, xmin)
        ymin = max(0, ymin)
        xmax = min(w, xmax)
        ymax = min(h, ymax)
        image[ymin:ymax, xmin:xmax] = mask_color
        return image

    return _cutout

In [12]:
def accuracy(output, target, topk=(1,)):
    """Computes the precision@k for the specified values of k"""
    maxk = max(topk)
    batch_size = target.size(0)

    _, pred = output.topk(maxk, 1, True, True)
    pred = pred.t()
    correct = pred.eq(target.view(1, -1).expand_as(pred))

    res = []
    for k in topk:
        correct_k = correct[:k].view(-1).float().sum(0)
        res.append(correct_k.mul_(100.0 / batch_size))
    return res

In [13]:
if __name__ == '__main__':
    main(hparam)

Current CPU Random Seed: 52
Current GPU Random Seed: 52
Test Data: torch.Size([40000, 28, 28])
Train Data: torch.Size([30000, 28, 28])
(Rearranged)Train: 30000	 Test: 40000

===> Training on Single-GPU!
Number of model parameters: 11708362


/home/jwserver/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:12: DeprecationWarning: 'saved_variables' is deprecated; use 'saved_tensors'
  if sys.path[0] == '':


Epoch: [0][0/118]	Time 0.986 (0.986)	Loss 2.3051 (2.3051)	Prec@1 12.109 (12.109)
Epoch: [0][10/118]	Time 0.248 (0.306)	Loss 1.1098 (1.6080)	Prec@1 60.156 (42.756)
Epoch: [0][20/118]	Time 0.249 (0.279)	Loss 0.9708 (1.3352)	Prec@1 60.938 (52.269)
Epoch: [0][30/118]	Time 0.249 (0.269)	Loss 0.7356 (1.1838)	Prec@1 72.266 (57.334)
Epoch: [0][40/118]	Time 0.249 (0.264)	Loss 0.6966 (1.0692)	Prec@1 74.219 (60.966)
Epoch: [0][50/118]	Time 0.248 (0.261)	Loss 0.7011 (0.9937)	Prec@1 76.562 (63.519)
Epoch: [0][60/118]	Time 0.251 (0.259)	Loss 0.6522 (0.9386)	Prec@1 73.047 (65.478)
Epoch: [0][70/118]	Time 0.249 (0.258)	Loss 0.6318 (0.8901)	Prec@1 76.562 (67.121)
Epoch: [0][80/118]	Time 0.250 (0.257)	Loss 0.6411 (0.8512)	Prec@1 77.344 (68.591)
Epoch: [0][90/118]	Time 0.250 (0.256)	Loss 0.5404 (0.8197)	Prec@1 76.562 (69.677)
Epoch: [0][100/118]	Time 0.250 (0.256)	Loss 0.4939 (0.7910)	Prec@1 80.469 (70.680)
Epoch: [0][110/118]	Time 0.250 (0.255)	Loss 0.5004 (0.7662)	Prec@1 82.422 (71.618)
Test: [0/157]	T

Test: [60/157]	Time 0.076 (0.079)	Loss 0.2771 (0.3035)	Prec@1 89.453 (89.184)
Test: [70/157]	Time 0.076 (0.079)	Loss 0.3438 (0.3053)	Prec@1 85.938 (89.096)
Test: [80/157]	Time 0.077 (0.079)	Loss 0.2506 (0.3056)	Prec@1 89.844 (89.038)
Test: [90/157]	Time 0.077 (0.079)	Loss 0.3411 (0.3056)	Prec@1 89.844 (89.032)
Test: [100/157]	Time 0.077 (0.078)	Loss 0.2473 (0.3061)	Prec@1 91.016 (88.943)
Test: [110/157]	Time 0.076 (0.078)	Loss 0.2821 (0.3065)	Prec@1 89.844 (88.901)
Test: [120/157]	Time 0.076 (0.078)	Loss 0.2496 (0.3043)	Prec@1 91.797 (88.991)
Test: [130/157]	Time 0.076 (0.078)	Loss 0.4027 (0.3054)	Prec@1 85.547 (88.970)
Test: [140/157]	Time 0.076 (0.078)	Loss 0.3770 (0.3051)	Prec@1 87.500 (88.957)
Test: [150/157]	Time 0.076 (0.078)	Loss 0.3245 (0.3073)	Prec@1 88.672 (88.938)
 * Prec@1 88.960
Epoch: [4][0/118]	Time 0.235 (0.235)	Loss 0.3160 (0.3160)	Prec@1 86.719 (86.719)
Epoch: [4][10/118]	Time 0.255 (0.253)	Loss 0.2672 (0.2852)	Prec@1 91.797 (89.098)
Epoch: [4][20/118]	Time 0.254 (0.2

Epoch: [7][80/118]	Time 0.255 (0.255)	Loss 0.2597 (0.2525)	Prec@1 89.062 (90.818)
Epoch: [7][90/118]	Time 0.256 (0.255)	Loss 0.1784 (0.2494)	Prec@1 92.969 (90.968)
Epoch: [7][100/118]	Time 0.254 (0.255)	Loss 0.2139 (0.2464)	Prec@1 91.406 (91.043)
Epoch: [7][110/118]	Time 0.254 (0.255)	Loss 0.2275 (0.2425)	Prec@1 90.625 (91.160)
Test: [0/157]	Time 0.264 (0.264)	Loss 0.3104 (0.3104)	Prec@1 89.453 (89.453)
Test: [10/157]	Time 0.078 (0.094)	Loss 0.3680 (0.3491)	Prec@1 85.156 (88.636)
Test: [20/157]	Time 0.078 (0.086)	Loss 0.2772 (0.3380)	Prec@1 91.406 (89.211)
Test: [30/157]	Time 0.077 (0.083)	Loss 0.2924 (0.3366)	Prec@1 90.625 (89.327)
Test: [40/157]	Time 0.077 (0.082)	Loss 0.4272 (0.3354)	Prec@1 86.719 (89.367)
Test: [50/157]	Time 0.077 (0.081)	Loss 0.2525 (0.3304)	Prec@1 91.016 (89.499)
Test: [60/157]	Time 0.077 (0.080)	Loss 0.2999 (0.3336)	Prec@1 90.625 (89.415)
Test: [70/157]	Time 0.077 (0.080)	Loss 0.2777 (0.3341)	Prec@1 90.234 (89.464)
Test: [80/157]	Time 0.077 (0.079)	Loss 0.3142 (

...

Epoch: [1785][50/118]	Time 0.255 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1785][60/118]	Time 0.254 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1785][70/118]	Time 0.254 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1785][80/118]	Time 0.254 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1785][90/118]	Time 0.255 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1785][100/118]	Time 0.253 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1785][110/118]	Time 0.254 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Test: [0/157]	Time 0.251 (0.251)	Loss 0.3606 (0.3606)	Prec@1 93.359 (93.359)
Test: [10/157]	Time 0.076 (0.092)	Loss 0.3024 (0.3746)	Prec@1 93.750 (93.288)
Test: [20/157]	Time 0.076 (0.085)	Loss 0.2631 (0.3437)	Prec@1 95.312 (93.806)
Test: [30/157]	Time 0.077 (0.082)	Loss 0.2646 (0.3346)	Prec@1 94.922 (93.826)
Test: [40/157]	Time 0.077 (0.081)	Loss 0.3102 (0.3453)	Prec@1 95.312 (93.655)


Test: [90/157]	Time 0.077 (0.079)	Loss 0.1879 (0.3455)	Prec@1 94.531 (93.617)
Test: [100/157]	Time 0.077 (0.078)	Loss 0.2746 (0.3504)	Prec@1 95.312 (93.572)
Test: [110/157]	Time 0.077 (0.078)	Loss 0.3522 (0.3483)	Prec@1 94.141 (93.602)
Test: [120/157]	Time 0.077 (0.078)	Loss 0.3194 (0.3458)	Prec@1 93.750 (93.631)
Test: [130/157]	Time 0.077 (0.078)	Loss 0.3268 (0.3418)	Prec@1 92.578 (93.661)
Test: [140/157]	Time 0.077 (0.078)	Loss 0.4287 (0.3406)	Prec@1 93.359 (93.661)
Test: [150/157]	Time 0.077 (0.078)	Loss 0.3504 (0.3394)	Prec@1 92.578 (93.680)
 * Prec@1 93.640
Epoch: [1789][0/118]	Time 0.234 (0.234)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1789][10/118]	Time 0.254 (0.252)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1789][20/118]	Time 0.255 (0.253)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1789][30/118]	Time 0.255 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1789][40/118]	Time 0.256 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.00

Epoch: [1792][80/118]	Time 0.255 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1792][90/118]	Time 0.253 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1792][100/118]	Time 0.253 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1792][110/118]	Time 0.254 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Test: [0/157]	Time 0.246 (0.246)	Loss 0.3872 (0.3872)	Prec@1 92.578 (92.578)
Test: [10/157]	Time 0.077 (0.092)	Loss 0.2021 (0.3095)	Prec@1 95.703 (93.857)
Test: [20/157]	Time 0.077 (0.085)	Loss 0.4242 (0.3364)	Prec@1 91.797 (93.564)
Test: [30/157]	Time 0.077 (0.082)	Loss 0.3178 (0.3450)	Prec@1 94.531 (93.548)
Test: [40/157]	Time 0.077 (0.081)	Loss 0.1319 (0.3447)	Prec@1 96.094 (93.455)
Test: [50/157]	Time 0.077 (0.080)	Loss 0.3712 (0.3488)	Prec@1 92.578 (93.459)
Test: [60/157]	Time 0.077 (0.079)	Loss 0.1678 (0.3432)	Prec@1 96.094 (93.584)
Test: [70/157]	Time 0.077 (0.079)	Loss 0.2727 (0.3427)	Prec@1 95.312 (93.645)
Test: [80/157]	Time 0.077 (

Test: [120/157]	Time 0.077 (0.078)	Loss 0.4820 (0.3362)	Prec@1 91.016 (93.631)
Test: [130/157]	Time 0.077 (0.078)	Loss 0.4840 (0.3385)	Prec@1 91.797 (93.643)
Test: [140/157]	Time 0.077 (0.078)	Loss 0.5261 (0.3420)	Prec@1 91.016 (93.606)
Test: [150/157]	Time 0.076 (0.078)	Loss 0.2671 (0.3440)	Prec@1 95.703 (93.600)
 * Prec@1 93.640
Epoch: [1796][0/118]	Time 0.243 (0.243)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1796][10/118]	Time 0.254 (0.253)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1796][20/118]	Time 0.254 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1796][30/118]	Time 0.254 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1796][40/118]	Time 0.253 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1796][50/118]	Time 0.254 (0.254)	Loss 0.0003 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1796][60/118]	Time 0.254 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Epoch: [1796][70/118]	Time 0.253 (0.254)	Loss 0.0002 (0.000

Epoch: [1799][110/118]	Time 0.255 (0.254)	Loss 0.0002 (0.0002)	Prec@1 100.000 (100.000)
Test: [0/157]	Time 0.232 (0.232)	Loss 0.2663 (0.2663)	Prec@1 94.531 (94.531)
Test: [10/157]	Time 0.076 (0.091)	Loss 0.3554 (0.3296)	Prec@1 92.969 (93.643)
Test: [20/157]	Time 0.077 (0.084)	Loss 0.4217 (0.3402)	Prec@1 92.969 (93.731)
Test: [30/157]	Time 0.077 (0.082)	Loss 0.2713 (0.3399)	Prec@1 95.703 (93.662)
Test: [40/157]	Time 0.077 (0.081)	Loss 0.3062 (0.3399)	Prec@1 94.141 (93.693)
Test: [50/157]	Time 0.077 (0.080)	Loss 0.3592 (0.3477)	Prec@1 93.359 (93.627)
Test: [60/157]	Time 0.077 (0.080)	Loss 0.3114 (0.3469)	Prec@1 95.703 (93.667)
Test: [70/157]	Time 0.076 (0.079)	Loss 0.5781 (0.3510)	Prec@1 92.578 (93.629)
Test: [80/157]	Time 0.077 (0.079)	Loss 0.2816 (0.3472)	Prec@1 94.922 (93.673)
Test: [90/157]	Time 0.077 (0.079)	Loss 0.2380 (0.3454)	Prec@1 93.750 (93.703)
Test: [100/157]	Time 0.077 (0.078)	Loss 0.3179 (0.3423)	Prec@1 94.531 (93.742)
Test: [110/157]	Time 0.076 (0.078)	Loss 0.3596 (0.3463

Best accuracy: 93.725